In [1]:
# Cell 1: Import libraries
import pandas as pd
import numpy as np
import os
import shutil

In [3]:
data_folder = "/Users/izzymohamed/Desktop/MLPData/CT"
OASIS3_unchanged_CDR_cognitively_healthy_path = data_folder + "/OASIS3_unchanged_CDR_cognitively_healthy.csv"
OASIS3_UDSb4_cdr_path = data_folder + "/OASIS3_UDSb4_cdr.csv"

In [4]:
# Mapping of CDR numerical values to labels
cdr_mapping = {
    0: "non-demented",
    0.5: "very-mild-dementia",
    1: "mild-dementia",
    2: "moderate-dementia",
    "": "unknown"  # Add a new category
    }

def get_cdr_label(cdr_value):

    # Convert the CDR value to a label using the mapping
    # Use the get method to handle cases where cdr_value is not in cdr_mapping
    return cdr_mapping.get(cdr_value, 'Unknown')

In [5]:
# This function is used to create the categories folders.
def create_categories_folders(preprocessed_data_path):
    
    # Define the paths for the different dementia levels
    categories_file_paths = [os.path.join(preprocessed_data_path, category) for category in cdr_mapping.values()]

    # Check if the directories exist, if not create them.
    for category, category_path in zip(cdr_mapping.values(), categories_file_paths):
        if not os.path.exists(category_path):
            os.makedirs(category_path)
            print(f"Created folder: {category_path}")
        else:
            print(f"Folder already exists: {category_path}")

In [6]:

original_preprocessed_images_dir = os.path.join(data_folder, 'Preprocessed')
categorised_preprocessed_image_dir = os.path.join(data_folder, 'Preprocessed_Categories')

# Ensure the categorized directory exists
os.makedirs(categorised_preprocessed_image_dir, exist_ok=True)
print(f"Ensured or created folder: {categorised_preprocessed_image_dir}")

# Assuming create_categories_folders() creates necessary category directories
create_categories_folders(categorised_preprocessed_image_dir)

Ensured or created folder: /Users/izzymohamed/Desktop/MLPData/CT/Preprocessed_Categories
Created folder: /Users/izzymohamed/Desktop/MLPData/CT/Preprocessed_Categories/non-demented
Created folder: /Users/izzymohamed/Desktop/MLPData/CT/Preprocessed_Categories/very-mild-dementia
Created folder: /Users/izzymohamed/Desktop/MLPData/CT/Preprocessed_Categories/mild-dementia
Created folder: /Users/izzymohamed/Desktop/MLPData/CT/Preprocessed_Categories/moderate-dementia
Created folder: /Users/izzymohamed/Desktop/MLPData/CT/Preprocessed_Categories/unknown


In [7]:
# Collect all PNG files into a list
png_files = [(root, file) for root, dirs, files in os.walk(data_folder) 
            for file in files if file.endswith("png") and file != ".DS_Store"]

print(f"Total PNG files: {len(png_files)}")

files_dictionary = {file: os.path.join(root, file) for root, file in png_files}

# convert dictionary to dataframe
files_directory_df = pd.DataFrame(list(files_dictionary.items()),columns = ['file','file_full_path'])
# Add OASISID column to the dataframe
files_directory_df['OASISID'] = files_directory_df['file'].str.extract(r'(OAS\d{5})', expand=False).str.strip()


# Add Day column to the dataframe id OASISID contain OAS3 or OAS4
if "OAS3" in files_directory_df['file'].values.any() or "OAS4" in files_directory_df['file'].values.any():
    files_directory_df['CLINICALDATAID'] = files_directory_df['OASISID'] + "_scan_" + files_directory_df['file'].str.extract(r'(d\d{4})', expand=False).str.strip()
    files_directory_df['days_to_visit'] = files_directory_df['file'].str.extract(r'(d\d{5})', expand=False).str.strip().apply(lambda x: int(x.split('d')[1]) if isinstance(x, str) else 0)

print(f"Total Files Dictionary Length: {len(files_dictionary)}")

Total PNG files: 79558
Total Files Dictionary Length: 79558


In [8]:
files_directory_df

file  \
0      Slice_x_1_OAS31245_CT_d0139_imgsub-OAS31245_se...   
1      Slice_x_7_OAS31245_CT_d0139_imgsub-OAS31245_se...   
2      Slice_x_13_OAS31245_CT_d0139_imgsub-OAS31245_s...   
3      Slice_x_15_OAS31245_CT_d0139_imgsub-OAS31245_s...   
4      Slice_x_19_OAS31245_CT_d0139_imgsub-OAS31245_s...   
...                                                  ...   
79553  Slice_x_34_OAS30191_CT_d3595_imgsub-OAS30191_s...   
79554  Slice_x_19_OAS30191_CT_d3595_imgsub-OAS30191_s...   
79555  Slice_x_11_OAS30191_CT_d3595_imgsub-OAS30191_s...   
79556  Slice_x_20_OAS30191_CT_d3595_imgsub-OAS30191_s...   
79557  Slice_x_37_OAS30191_CT_d3595_imgsub-OAS30191_s...   

                                          file_full_path   OASISID  \
0      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS31245   
1      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS31245   
2      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS31245   
3      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS31245   
4      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS31245   
...                                                  ...       ...   
79553  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS30191   
79554  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS30191   
79555  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS30191   
79556  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS30191   
79557  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS30191   

            CLINICALDATAID  days_to_visit  
0      OAS31245_scan_d0139              0  
1      OAS31245_scan_d0139              0  
2      OAS31245_scan_d0139              0  
3      OAS31245_scan_d0139              0  
4      OAS31245_scan_d0139              0  
...                    ...            ...  
79553  OAS30191_scan_d3595              0  
79554  OAS30191_scan_d3595              0  
79555  OAS30191_scan_d3595              0  
79556  OAS30191_scan_d3595              0  
79557  OAS30191_scan_d3595              0  

[79558 rows x 5 columns]

In [9]:
OASIS3_unchanged_CDR_cognitively_healthy = pd.read_csv(OASIS3_unchanged_CDR_cognitively_healthy_path)

In [10]:
OASIS3_UDSb4_cdr = pd.read_csv(OASIS3_UDSb4_cdr_path)

In [11]:
# Check if the OASISID is in the OASIS3_unchanged_CDR_cognitively_healthy
# if yes move to categorised_preprocessed_image_dir = os.path.join(data_folder, 'Preprocessed_Categories', get_cdr_label(

for index, row in files_directory_df.iterrows():
    if row['OASISID'] in OASIS3_unchanged_CDR_cognitively_healthy['OASIS3_id'].values:
        # Get OASIS3_unchanged_CDR_cognitively_healthy['Max of CDRTOT'] to feed to get_cdr_label
        label_id = OASIS3_unchanged_CDR_cognitively_healthy[OASIS3_unchanged_CDR_cognitively_healthy['OASIS3_id'] == row['OASISID']]['Max of CDRTOT'].values[0]
        # Move the file to the respective category folder
        source = row['file_full_path']
        destination = os.path.join(categorised_preprocessed_image_dir, get_cdr_label(label_id), row['file'])
        shutil.move(source, destination)
        # Remove row from the dataframe
        files_directory_df.drop(index, inplace=True)

In [12]:
OASIS3_UDSb4_cdr

OASISID   OASIS_session_label  days_to_visit  age at visit  MMSE  \
0     OAS30001  OAS30001_UDSb4_d0000              0         65.19  28.0   
1     OAS30001  OAS30001_UDSb4_d0339            339         66.12  28.0   
2     OAS30001  OAS30001_UDSb4_d0722            722         67.17  30.0   
3     OAS30001  OAS30001_UDSb4_d1106           1106         68.22  30.0   
4     OAS30001  OAS30001_UDSb4_d1456           1456         69.18  30.0   
...        ...                   ...            ...           ...   ...   
8621  OAS31472  OAS31472_UDSb4_d0826            826         69.53   NaN   
8622  OAS31473  OAS31473_UDSb4_d0000              0         56.61  30.0   
8623  OAS31473  OAS31473_UDSb4_d1142           1142         59.74   NaN   
8624  OAS31474  OAS31474_UDSb4_d0000              0         81.84  22.0   
8625  OAS31474  OAS31474_UDSb4_d0732            732         83.85  23.0   

      memory  orient  judgment  commun  homehobb  ...  dx1_code  dx2_code  \
0        0.0     0.0       0.0     0.0       0.0  ...       1.0       NaN   
1        0.0     0.0       0.0     0.0       0.0  ...       1.0       NaN   
2        0.0     0.0       0.0     0.0       0.0  ...       1.0       NaN   
3        0.0     0.0       0.0     0.0       0.0  ...       1.0       NaN   
4        0.0     0.0       0.0     0.0       0.0  ...       1.0       NaN   
...      ...     ...       ...     ...       ...  ...       ...       ...   
8621     0.0     0.0       0.0     0.0       0.0  ...       1.0       NaN   
8622     0.0     0.0       0.0     0.0       0.0  ...       1.0       NaN   
8623     0.5     0.0       0.0     0.0       0.0  ...       2.0       NaN   
8624     0.5     0.0       0.0     0.0       0.0  ...     150.0       NaN   
8625     1.0     1.0       0.5     0.5       1.0  ...       3.0       NaN   

      dx3_code  dx4_code  dx5_code                 dx1  dx2  dx3 dx4 dx5  
0          NaN       NaN       NaN  Cognitively normal    .    .   .   .  
1          NaN       NaN       NaN  Cognitively normal    .    .   .   .  
2          NaN       NaN       NaN  Cognitively normal    .    .   .   .  
3          NaN       NaN       NaN  Cognitively normal    .    .   .   .  
4          NaN       NaN       NaN  Cognitively normal    .    .   .   .  
...        ...       ...       ...                 ...  ...  ...  ..  ..  
8621       NaN       NaN       NaN  Cognitively normal    A    A   A   A  
8622       NaN       NaN       NaN  Cognitively normal    A    A   A   A  
8623       NaN       NaN       NaN  uncertain dementia    A    A   A   A  
8624       NaN       NaN       NaN  0.5 in memory only    A    A   A   A  
8625       NaN       NaN       NaN         AD Dementia    A    A   A   A  

[8626 rows x 23 columns]

In [13]:
# Copy with these columns 'OASISID', 'OASIS_session_label', 'days_to_visit', "CDRTOT"
OASIS3_UDSb4_cdr_copy = OASIS3_UDSb4_cdr.copy()[['OASISID', 'OASIS_session_label', 'days_to_visit', "CDRTOT"]]

In [14]:
OASIS3_UDSb4_cdr_copy

OASISID   OASIS_session_label  days_to_visit  CDRTOT
0     OAS30001  OAS30001_UDSb4_d0000              0     0.0
1     OAS30001  OAS30001_UDSb4_d0339            339     0.0
2     OAS30001  OAS30001_UDSb4_d0722            722     0.0
3     OAS30001  OAS30001_UDSb4_d1106           1106     0.0
4     OAS30001  OAS30001_UDSb4_d1456           1456     0.0
...        ...                   ...            ...     ...
8621  OAS31472  OAS31472_UDSb4_d0826            826     0.0
8622  OAS31473  OAS31473_UDSb4_d0000              0     0.0
8623  OAS31473  OAS31473_UDSb4_d1142           1142     0.5
8624  OAS31474  OAS31474_UDSb4_d0000              0     0.5
8625  OAS31474  OAS31474_UDSb4_d0732            732     1.0

[8626 rows x 4 columns]

In [15]:
# Cell 2: Define the main function and any additional functions
def matching_up_the_data_upper_lower(scan_session_day, clinical_assesment_day, output_name, lower_bound, upper_bound):
    
    # Create a Day column from ID
    # Use the "dXXXX" value from the ID/label in the first column
    # pandas extract will pull that based on a regular expression no matter where it is.
   
    # Update scan_session_day to only consider subjects that are in both lists
    scan_session_day =scan_session_day.loc[scan_session_day['OASISID'].isin(clinical_assesment_day['OASISID'])]

    # Create and populate the dataframe
    for index, row in clinical_assesment_day.iterrows():
        mask = (scan_session_day['OASISID'] == row['OASISID']) & ((scan_session_day['days_to_visit'] < row['days_to_visit'] + upper_bound) & (scan_session_day['days_to_visit'] > row['days_to_visit'] - lower_bound))   
        for name in row.index:
            scan_session_day.loc[mask, name +'_clinical_assesment_day'] = row[name]
    
    # Drop rows of which a match was not found
    #scan_session_day.dropna(inplace=True)
    # clinical_assesment_day_firstcolumnname=clinical_assesment_day.columns.values[0] + "_clinical_assesment_day"
    # scan_session_day.dropna(subset=[clinical_assesment_day_firstcolumnname])
    #clinical_assesment_day.dropna(subset=[clinical_assesment_day_firstcolumnname])

    # scan_session_day.to_csv(output_name, index=False)
    return scan_session_day

In [16]:
match_up_df = matching_up_the_data_upper_lower(files_directory_df, OASIS3_UDSb4_cdr_copy, "output_name", 180, 180)

In [17]:
match_up_df

file  \
0      Slice_x_1_OAS31245_CT_d0139_imgsub-OAS31245_se...   
1      Slice_x_7_OAS31245_CT_d0139_imgsub-OAS31245_se...   
2      Slice_x_13_OAS31245_CT_d0139_imgsub-OAS31245_s...   
3      Slice_x_15_OAS31245_CT_d0139_imgsub-OAS31245_s...   
4      Slice_x_19_OAS31245_CT_d0139_imgsub-OAS31245_s...   
...                                                  ...   
79493  Slice_x_4_OAS30013_CT_d0102_imgsub-OAS30013_se...   
79494  Slice_x_45_OAS30013_CT_d0102_imgsub-OAS30013_s...   
79495  Slice_x_59_OAS30013_CT_d0102_imgsub-OAS30013_s...   
79496  Slice_x_52_OAS30013_CT_d0102_imgsub-OAS30013_s...   
79497  Slice_x_7_OAS30013_CT_d0102_imgsub-OAS30013_se...   

                                          file_full_path   OASISID  \
0      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS31245   
1      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS31245   
2      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS31245   
3      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS31245   
4      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS31245   
...                                                  ...       ...   
79493  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS30013   
79494  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS30013   
79495  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS30013   
79496  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS30013   
79497  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS30013   

            CLINICALDATAID  days_to_visit OASISID_clinical_assesment_day  \
0      OAS31245_scan_d0139              0                       OAS31245   
1      OAS31245_scan_d0139              0                       OAS31245   
2      OAS31245_scan_d0139              0                       OAS31245   
3      OAS31245_scan_d0139              0                       OAS31245   
4      OAS31245_scan_d0139              0                       OAS31245   
...                    ...            ...                            ...   
79493  OAS30013_scan_d0102              0                       OAS30013   
79494  OAS30013_scan_d0102              0                       OAS30013   
79495  OAS30013_scan_d0102              0                       OAS30013   
79496  OAS30013_scan_d0102              0                       OAS30013   
79497  OAS30013_scan_d0102              0                       OAS30013   

      OASIS_session_label_clinical_assesment_day  \
0                           OAS31245_UDSb4_d0000   
1                           OAS31245_UDSb4_d0000   
2                           OAS31245_UDSb4_d0000   
3                           OAS31245_UDSb4_d0000   
4                           OAS31245_UDSb4_d0000   
...                                          ...   
79493                       OAS30013_UDSb4_d0000   
79494                       OAS30013_UDSb4_d0000   
79495                       OAS30013_UDSb4_d0000   
79496                       OAS30013_UDSb4_d0000   
79497                       OAS30013_UDSb4_d0000   

       days_to_visit_clinical_assesment_day  CDRTOT_clinical_assesment_day  
0                                       0.0                            0.5  
1                                       0.0                            0.5  
2                                       0.0                            0.5  
3                                       0.0                            0.5  
4                                       0.0                            0.5  
...                                     ...                            ...  
79493                                   0.0                            0.5  
79494                                   0.0                            0.5  
79495                                   0.0                            0.5  
79496                                   0.0                            0.5  
79497                                   0.0                            0.5  

[22196 rows x 9 columns]

In [18]:
match_up_df['CDRTOT_clinical_assesment_day'] = pd.to_numeric(match_up_df['CDRTOT_clinical_assesment_day'], errors='coerce')

In [19]:
# Create a new column in the dataframe with the CDR label
match_up_df['CDRTOT_clinical_assesment_day_label'] = match_up_df['CDRTOT_clinical_assesment_day'].apply(get_cdr_label)

In [20]:
match_up_df

file  \
0      Slice_x_1_OAS31245_CT_d0139_imgsub-OAS31245_se...   
1      Slice_x_7_OAS31245_CT_d0139_imgsub-OAS31245_se...   
2      Slice_x_13_OAS31245_CT_d0139_imgsub-OAS31245_s...   
3      Slice_x_15_OAS31245_CT_d0139_imgsub-OAS31245_s...   
4      Slice_x_19_OAS31245_CT_d0139_imgsub-OAS31245_s...   
...                                                  ...   
79493  Slice_x_4_OAS30013_CT_d0102_imgsub-OAS30013_se...   
79494  Slice_x_45_OAS30013_CT_d0102_imgsub-OAS30013_s...   
79495  Slice_x_59_OAS30013_CT_d0102_imgsub-OAS30013_s...   
79496  Slice_x_52_OAS30013_CT_d0102_imgsub-OAS30013_s...   
79497  Slice_x_7_OAS30013_CT_d0102_imgsub-OAS30013_se...   

                                          file_full_path   OASISID  \
0      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS31245   
1      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS31245   
2      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS31245   
3      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS31245   
4      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS31245   
...                                                  ...       ...   
79493  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS30013   
79494  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS30013   
79495  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS30013   
79496  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS30013   
79497  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...  OAS30013   

            CLINICALDATAID  days_to_visit OASISID_clinical_assesment_day  \
0      OAS31245_scan_d0139              0                       OAS31245   
1      OAS31245_scan_d0139              0                       OAS31245   
2      OAS31245_scan_d0139              0                       OAS31245   
3      OAS31245_scan_d0139              0                       OAS31245   
4      OAS31245_scan_d0139              0                       OAS31245   
...                    ...            ...                            ...   
79493  OAS30013_scan_d0102              0                       OAS30013   
79494  OAS30013_scan_d0102              0                       OAS30013   
79495  OAS30013_scan_d0102              0                       OAS30013   
79496  OAS30013_scan_d0102              0                       OAS30013   
79497  OAS30013_scan_d0102              0                       OAS30013   

      OASIS_session_label_clinical_assesment_day  \
0                           OAS31245_UDSb4_d0000   
1                           OAS31245_UDSb4_d0000   
2                           OAS31245_UDSb4_d0000   
3                           OAS31245_UDSb4_d0000   
4                           OAS31245_UDSb4_d0000   
...                                          ...   
79493                       OAS30013_UDSb4_d0000   
79494                       OAS30013_UDSb4_d0000   
79495                       OAS30013_UDSb4_d0000   
79496                       OAS30013_UDSb4_d0000   
79497                       OAS30013_UDSb4_d0000   

       days_to_visit_clinical_assesment_day  CDRTOT_clinical_assesment_day  \
0                                       0.0                            0.5   
1                                       0.0                            0.5   
2                                       0.0                            0.5   
3                                       0.0                            0.5   
4                                       0.0                            0.5   
...                                     ...                            ...   
79493                                   0.0                            0.5   
79494                                   0.0                            0.5   
79495                                   0.0                            0.5   
79496                                   0.0                            0.5   
79497                                   0.0                            0.5   

      CDRTOT_cl

In [21]:
def create_df(new_data_df, files_dictionary, categorised_preprocessed_image_dir):
    # Create a mapping of file to label_id to avoid repeated .loc calls
    file_to_label_map = new_data_df.set_index('file')['CDRTOT_clinical_assesment_day_label'].to_dict()

    save_rows = [{
        'file': file,
        'file_full_path': file_full_path,
        'dest_item': os.path.join(categorised_preprocessed_image_dir, file_to_label_map.get(file, 'unknown'), file)
    } for file, file_full_path in files_dictionary.items() if file in file_to_label_map]

    # Save save_rows to a csv file
    save_df = pd.DataFrame(save_rows, columns=['file', 'file_full_path', 'dest_item'])

    return save_df

In [22]:
file_moves_df = create_df(match_up_df,files_dictionary, categorised_preprocessed_image_dir)

In [23]:
file_moves_df

file  \
0      Slice_x_1_OAS31245_CT_d0139_imgsub-OAS31245_se...   
1      Slice_x_7_OAS31245_CT_d0139_imgsub-OAS31245_se...   
2      Slice_x_13_OAS31245_CT_d0139_imgsub-OAS31245_s...   
3      Slice_x_15_OAS31245_CT_d0139_imgsub-OAS31245_s...   
4      Slice_x_19_OAS31245_CT_d0139_imgsub-OAS31245_s...   
...                                                  ...   
22191  Slice_x_4_OAS30013_CT_d0102_imgsub-OAS30013_se...   
22192  Slice_x_45_OAS30013_CT_d0102_imgsub-OAS30013_s...   
22193  Slice_x_59_OAS30013_CT_d0102_imgsub-OAS30013_s...   
22194  Slice_x_52_OAS30013_CT_d0102_imgsub-OAS30013_s...   
22195  Slice_x_7_OAS30013_CT_d0102_imgsub-OAS30013_se...   

                                          file_full_path  \
0      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...   
1      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...   
2      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...   
3      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...   
4      /Users/izzymohamed/Desktop/MLPData/CT/Perproce...   
...                                                  ...   
22191  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...   
22192  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...   
22193  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...   
22194  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...   
22195  /Users/izzymohamed/Desktop/MLPData/CT/Perproce...   

                                               dest_item  
0      /Users/izzymohamed/Desktop/MLPData/CT/Preproce...  
1      /Users/izzymohamed/Desktop/MLPData/CT/Preproce...  
2      /Users/izzymohamed/Desktop/MLPData/CT/Preproce...  
3      /Users/izzymohamed/Desktop/MLPData/CT/Preproce...  
4      /Users/izzymohamed/Desktop/MLPData/CT/Preproce...  
...                                                  ...  
22191  /Users/izzymohamed/Desktop/MLPData/CT/Preproce...  
22192  /Users/izzymohamed/Desktop/MLPData/CT/Preproce...  
22193  /Users/izzymohamed/Desktop/MLPData/CT/Preproce...  
22194  /Users/izzymohamed/Desktop/MLPData/CT/Preproce...  
22195  /Users/izzymohamed/Desktop/MLPData/CT/Preproce...  

[22196 rows x 3 columns]

In [24]:
# This function is used to move the images into the categories.
def move_images_into_categories(data_folder, file_moves_df):
    original_preprocessed_images_dir = os.path.join(data_folder, 'Preprocessed')
    categorised_preprocessed_image_dir = os.path.join(data_folder, 'Preprocessed_Categories')

    # Ensure the categorized directory exists
    os.makedirs(categorised_preprocessed_image_dir, exist_ok=True)
    print(f"Ensured or created folder: {categorised_preprocessed_image_dir}")

    # Assuming create_categories_folders() creates necessary category directories
    create_categories_folders(categorised_preprocessed_image_dir)

    # Collect all PNG files into a list
    png_files = [(root, file) for root, dirs, files in os.walk(original_preprocessed_images_dir) 
             for file in files if file.endswith("png") and file != ".DS_Store"]

    print(f"Total PNG files: {len(png_files)}")

    # Assuming create_df() function returns a DataFrame with 'file_full_path' and 'dest_item' for each file
    # file_moves_df = create_df(match_up_df, categorised_preprocessed_image_dir)

    print(f"DataFrame rows (file moves planned): {len(file_moves_df)}")

    # Move files based on the DataFrame
    for index, row in file_moves_df.iterrows():
        dest_dir = os.path.dirname(row["dest_item"])
        os.makedirs(dest_dir, exist_ok=True)  # Ensure destination directory exists

        if os.path.exists(row["dest_item"]):
            if os.path.isdir(row["dest_item"]):
                shutil.rmtree(row["dest_item"])
            else:
                os.remove(row["dest_item"])
        
        shutil.move(row["file_full_path"], row["dest_item"])
        print(f"Moved: {row['file_full_path']} to {row['dest_item']}")

    print(f"Completed moving {len(file_moves_df)} files.")

In [25]:
move_images_into_categories(data_folder, file_moves_df)

Ensured or created folder: /Users/izzymohamed/Desktop/MLPData/CT/Preprocessed_Categories
Folder already exists: /Users/izzymohamed/Desktop/MLPData/CT/Preprocessed_Categories/non-demented
Folder already exists: /Users/izzymohamed/Desktop/MLPData/CT/Preprocessed_Categories/very-mild-dementia
Folder already exists: /Users/izzymohamed/Desktop/MLPData/CT/Preprocessed_Categories/mild-dementia
Folder already exists: /Users/izzymohamed/Desktop/MLPData/CT/Preprocessed_Categories/moderate-dementia
Folder already exists: /Users/izzymohamed/Desktop/MLPData/CT/Preprocessed_Categories/unknown
Total PNG files: 0
DataFrame rows (file moves planned): 22196
Moved: /Users/izzymohamed/Desktop/MLPData/CT/Perprocessed/Data/OAS31245_CT_d0139/Slice_x_1_OAS31245_CT_d0139_imgsub-OAS31245_sess-d0139_run-01_CT.nii.gz.png to /Users/izzymohamed/Desktop/MLPData/CT/Preprocessed_Categories/very-mild-dementia/Slice_x_1_OAS31245_CT_d0139_imgsub-OAS31245_sess-d0139_run-01_CT.nii.gz.png
Moved: /Users/izzymohamed/Desktop/M